# Pipeline for image size estimation

Imports

In [27]:
import os
from pathlib import Path
import cv2
import matplotlib.pyplot as plt
import random
import numpy as np
from segment_anything import sam_model_registry, SamPredictor

### Step 1: Load images

In [28]:
# path to directory of images
directory = Path('../data/6_16')
images = []

# iterate files in directory
for idx, f in enumerate(os.listdir(directory)):
    file = os.path.join(directory, f)
    # assert valid file
    if os.path.isfile(file):
        # load image
        im = cv2.imread(file)
        im = cv2.cvtColor(im, cv2.COLOR_BGR2RGB)
        # add to list
        images.append(im)

print(f"loaded {len(images)} images")

loaded 8 images


Some helper functions for displaying images

In [67]:
def get_box(im):
    h, w, _ = im.shape
    x1, y1, x2, y2 = 400, 400, w-400, h-400
    input_box = np.array([x1, y1, x2, y2])
    return input_box

def show_box(box, ax):
    x0, y0 = box[0], box[1]
    w, h = box[2] - box[0], box[3] - box[1]
    ax.add_patch(plt.Rectangle((x0, y0), w, h, edgecolor='red', facecolor=(0,0,0,0), lw=2))

def show_mask(mask, ax, random_color=False):
    if random_color:
        color = np.concatenate([np.random.random(3), np.array([0.6])], axis=0)
    else:
        color = np.array([30/255, 144/255, 255/255, 0.6])
    h, w = mask.shape[-2:]
    mask_image = mask.reshape(h, w, 1) * color.reshape(1, 1, -1)
    ax.imshow(mask_image)

def show_points(coords, labels, ax, marker_size=375):
    pos_points = coords[labels==1]
    neg_points = coords[labels==0]
    ax.scatter(pos_points[:, 0], pos_points[:, 1], color='green', marker='*', s=marker_size, edgecolor='white', linewidth=1.25)
    ax.scatter(neg_points[:, 0], neg_points[:, 1], color='red', marker='*', s=marker_size, edgecolor='white', linewidth=1.25)

In [70]:
# function to help with visualizing images
def displayXimages(X, images, masks=None, showBox=False):
    # select three random indices
    random_indices = random.sample(range(len(images)), X)
    _, axes = plt.subplots(nrows=1, ncols=3, figsize=(X*6, 6))
    # add images to figure
    for i, rdx in enumerate(random_indices):
        axes[i].imshow(images[rdx])
        axes[i].axis('off')
        if masks is not None:
            show_mask(masks[rdx], axes[i])
        if showBox:
            input_box = get_box(im)
            show_box(input_box, axes[i])
    # display
    plt.tight_layout()
    plt.show()

In [50]:
displayXimages(3, images)

In [68]:
displayXimages(3, images, showBox=True)

Looks good!

### Step 2: Run images through SAM to prep for laser detection

Set up SAM

In [32]:
# select checkpoint and model type
sam_checkpoint = "../sam_vit_h_4b8939.pth"
model_type = "vit_h"

# define predictor
sam = sam_model_registry[model_type](checkpoint=sam_checkpoint)
predictor = SamPredictor(sam)

Iterate through images and get mask

In [69]:
im_masks = []
n = len(images)

for i, im in enumerate(images):
    print(f"getting mask {i+1} of {n}")
    input_box = get_box(im)
    # SAM
    predictor.set_image(im)
    masks, _, _ = predictor.predict(point_coords=None, point_labels=None,
                                    box=input_box[None, :], multimask_output=False)
    
    # overlay mask on original image
    im_masks.append(masks[0])

getting mask 1 of 8
getting mask 2 of 8
getting mask 3 of 8
getting mask 4 of 8
getting mask 5 of 8
getting mask 6 of 8
getting mask 7 of 8
getting mask 8 of 8


In [72]:
displayXimages(3, images, im_masks, showBox=True)